In [1]:
from continuous import components

v_bands length: 64


In [2]:
markets = [
    'BTCUSDT',
    'SOLUSDT',
    'PENDLEUSDT',
    'PHBUSDT',
    'MOVRUSDT',
    'ARKMUSDT',
    'JTOUSDT',
    'HIGHUSDT',
    'RNDRUSDT',
    'UMAUSDT',
    'PEOPLEUSDT',
    'TRBUSDT',
    'FTTUSDT',
    'FRONTUSDT',
    'KMDUSDT'
]

In [16]:
strategies = [
    'srsirev',
    # 'rsirev',
    'chanbreak',
    'ichitrend', 
    # 'emaroc', 
    'hmaroc'
    ]
# lookback window options: '4 years', '3 years', '2 years', '1 year', '6 months', '3 months', '1 month', '1 week'
trader = components.Trader(markets, dyn_weight_lb='1 week', fc_weighting=False, port_weights='flat', strat_list=strategies, keep_records=False, leverage=2, live=False)
trader.run_backtests(window='1 year',show_stats=True, plot_rtns=False, plot_forecast=True, plot_sharpe=False, plot_pnls=True, inspect_substrats=False)

Trader initialised at 10/05/2024 13:00:02 UTC
shape: (20, 17)
┌───────────────┬──────────┬──────────┬──────────┬───┬──────────────┬───────┬───────┬──────────────┐
│ timestamp     ┆ open     ┆ high     ┆ low      ┆ … ┆ vwma_200h    ┆ above ┆ below ┆ chan_break_8 │
│ ---           ┆ ---      ┆ ---      ┆ ---      ┆   ┆ ---          ┆ ---   ┆ ---   ┆ h_32_vwma_1h │
│ datetime[ns,  ┆ f64      ┆ f64      ┆ f64      ┆   ┆ f64          ┆ i64   ┆ i64   ┆ ---          │
│ UTC]          ┆          ┆          ┆          ┆   ┆              ┆       ┆       ┆ i32          │
╞═══════════════╪══════════╪══════════╪══════════╪═══╪══════════════╪═══════╪═══════╪══════════════╡
│ 2024-05-04    ┆ 62882.01 ┆ 63595.14 ┆ 62541.03 ┆ … ┆ 60730.665307 ┆ 0     ┆ 0     ┆ -1           │
│ 00:00:00 UTC  ┆          ┆          ┆          ┆   ┆              ┆       ┆       ┆              │
│ 2024-05-04    ┆ 62959.03 ┆ 64540.0  ┆ 62924.37 ┆ … ┆ 60730.500351 ┆ 0     ┆ 0     ┆ -1           │
│ 08:00:00 UTC  ┆          ┆ 

In [4]:
import polars as pl
results = pl.read_json('backtest_results.json')
results

shape: (120, 8)
┌─────────┬───────┬──────┬─────┬──────────┬───────────┬───────────┬───────────┐
│ lb      ┆ fc    ┆ port ┆ lev ┆ sharpe   ┆ total_rtn ┆ max_dd    ┆ avg_dd    │
│ ---     ┆ ---   ┆ ---  ┆ --- ┆ ---      ┆ ---       ┆ ---       ┆ ---       │
│ str     ┆ bool  ┆ str  ┆ i64 ┆ f64      ┆ f64       ┆ f64       ┆ f64       │
╞═════════╪═══════╪══════╪═════╪══════════╪═══════════╪═══════════╪═══════════╡
│ 1 week  ┆ true  ┆ flat ┆ 1   ┆ 0.981426 ┆ 1.717833  ┆ -0.182921 ┆ -0.096535 │
│ 1 week  ┆ true  ┆ perf ┆ 1   ┆ 0.570213 ┆ 1.662518  ┆ -0.34984  ┆ -0.195053 │
│ 1 week  ┆ false ┆ flat ┆ 1   ┆ 1.613628 ┆ 1.826349  ┆ -0.122873 ┆ -0.038973 │
│ 1 week  ┆ false ┆ perf ┆ 1   ┆ 1.071806 ┆ 1.798598  ┆ -0.182221 ┆ -0.094701 │
│ 1 week  ┆ true  ┆ flat ┆ 2   ┆ 0.863897 ┆ 2.667825  ┆ -0.343703 ┆ -0.188314 │
│ …       ┆ …     ┆ …    ┆ …   ┆ …        ┆ …         ┆ …         ┆ …         │
│ 2 years ┆ false ┆ perf ┆ 4   ┆ 0.854977 ┆ 2.632249  ┆ -0.304855 ┆ -0.175378 │
│ 2 years ┆ true  ┆ flat ┆ 5   ┆ 0.77727  ┆ 2.285238  ┆ -0.313549 ┆ -0.156844 │
│ 2 years ┆ true  ┆ perf ┆ 5   ┆ 0.367178 ┆ 1.579725  ┆ -0.497783 ┆ -0.185199 │
│ 2 years ┆ false ┆ flat ┆ 5   ┆ 1.242569 ┆ 12.52045  ┆ -0.491848 ┆ -0.207648 │
│ 2 years ┆ false ┆ perf ┆ 5   ┆ 0.79455  ┆ 3.145964  ┆ -0.366944 ┆ -0.216103 │
└─────────┴───────┴──────┴─────┴──────────┴───────────┴───────────┴───────────┘

In [10]:
thresh = 70
results.filter(
    pl.col('sharpe').rank() > thresh,
    pl.col('total_rtn').rank() > thresh,
    pl.col('max_dd').rank() > thresh,
    pl.col('avg_dd').rank() > thresh,
)

shape: (6, 8)
┌──────────┬───────┬──────┬─────┬──────────┬───────────┬──────────┬───────────┐
│ lb       ┆ fc    ┆ port ┆ lev ┆ sharpe   ┆ total_rtn ┆ max_dd   ┆ avg_dd    │
│ ---      ┆ ---   ┆ ---  ┆ --- ┆ ---      ┆ ---       ┆ ---      ┆ ---       │
│ str      ┆ bool  ┆ str  ┆ i64 ┆ f64      ┆ f64       ┆ f64      ┆ f64       │
╞══════════╪═══════╪══════╪═════╪══════════╪═══════════╪══════════╪═══════════╡
│ 1 week   ┆ false ┆ flat ┆ 2   ┆ 1.529868 ┆ 3.179989  ┆ -0.23229 ┆ -0.079624 │
│ 1 month  ┆ false ┆ flat ┆ 2   ┆ 1.528846 ┆ 3.178525  ┆ -0.23229 ┆ -0.079624 │
│ 3 months ┆ false ┆ flat ┆ 2   ┆ 1.529274 ┆ 3.179137  ┆ -0.23229 ┆ -0.079624 │
│ 6 months ┆ false ┆ flat ┆ 2   ┆ 1.528784 ┆ 3.178436  ┆ -0.23229 ┆ -0.079624 │
│ 1 year   ┆ false ┆ flat ┆ 2   ┆ 1.528784 ┆ 3.178436  ┆ -0.23229 ┆ -0.079624 │
│ 2 years  ┆ false ┆ flat ┆ 2   ┆ 1.526447 ┆ 3.175114  ┆ -0.23229 ┆ -0.079624 │
└──────────┴───────┴──────┴─────┴──────────┴───────────┴──────────┴───────────┘